In [ ]:
import os 
import re 
import pandas as pd

import numpy as np
from tqdm import tqdm
from collections import Counter
from utils import get_completion, num_tokens_from_string, compute_token_price
import pickle
import random



In [305]:
np.random.seed(42)
random.seed(42)
random.random()


0.6394267984578837

In [2]:

with open("../automatic_eval_results/all_autoeval_dfs.pkl", "rb") as infile:
    dfs = pickle.load(infile)

In [ ]:
def filter_rows_by_values(df, col, values):
    return df[df[col].isin(values)]

In [283]:
concat = pd.concat(dfs)
print(concat.shape)
concat.head()
before = concat.shape[0]

(8076, 4)


In [284]:
concat= filter_rows_by_values(concat, "IsQueryRelevant", ["SI", "NO"])
concat.shape
after = concat.shape[0]
print(f"Removed {before-after} items with invalid answers")

Removed 15 items with invalid answers


In [285]:
#create a new dataframe with the template of the questions to be evaluated by humans
man_eval_inputs = []
man_input_template = "{title}\n{text}\n\nDomanda:\n{question}"
for row in concat.itertuples():
    q = re.sub(r" secondo il testo\?", "?", row.Query[2:]).strip()
    example = re.sub(r"\{title\}", row._1  , re.sub(r"\{text\}", row.Passage, re.sub(r"\{question\}", q, man_input_template)))
    man_eval_inputs.append(example)

man_eval_df = pd.DataFrame(zip(concat["Articolo di riferimento"].tolist(), man_eval_inputs,concat["IsQueryRelevant"].tolist() ),
                            columns = ["Art.", "Quesito", "AutomaticEvaluation"])
man_eval_df.head()

Art.  \
0               Art. 1 Capacità giuridica   
1               Art. 1 Capacità giuridica   
2  Art. 2 Maggiore età. Capacità di agire   
3  Art. 2 Maggiore età. Capacità di agire   
4  Art. 2 Maggiore età. Capacità di agire   

                                             Quesito AutomaticEvaluation  
0  Art. 1 Capacità giuridica\nLa capacità giuridi...                  SI  
1  Art. 1 Capacità giuridica\nLa capacità giuridi...                  SI  
2  Art. 2 Maggiore età. Capacità di agire\nLa mag...                  SI  
3  Art. 2 Maggiore età. Capacità di agire\nLa mag...                  NO  
4  Art. 2 Maggiore età. Capacità di agire\nLa mag...                  SI

In [286]:
man_eval_df.shape

(8061, 3)

In [ ]:
# # gnerate random non overlapping slices of the complete dataframe
# random_sel = random.sample(man_eval_df.index.tolist(), 100)
# random_sets = [random_sel]

# for step in tqdm(range(79)): #man_eval_df.shape[0]//100 - 1
#     tmp_list = [i for i in man_eval_df.index.tolist() if i not in random_sel]
#     new_rand = random.sample(tmp_list, 100)
#     random_sets.append(new_rand)
#     random_sel += new_rand

# sampled_dfs = []
# for rset in random_sets:
#     sampled_dfs.append(man_eval_df.iloc[rset])

In [279]:
man_eval_df.shape[0]

8061

In [ ]:
#try a more efficient way
random.seed(42)
shuffled = man_eval_df.sample(frac = 1)
sampled_dfs = []
for step in range(0,8000, 100):
    sampled_dfs.append(shuffled.iloc[step:step+100])
    print(f"{step}-{step+100}")

0-100
100-200
200-300
300-400
400-500
500-600
600-700
700-800
800-900
900-1000
1000-1100
1100-1200
1200-1300
1300-1400
1400-1500
1500-1600
1600-1700
1700-1800
1800-1900
1900-2000
2000-2100
2100-2200
2200-2300
2300-2400
2400-2500
2500-2600
2600-2700
2700-2800
2800-2900
2900-3000
3000-3100
3100-3200
3200-3300
3300-3400
3400-3500
3500-3600
3600-3700
3700-3800
3800-3900
3900-4000
4000-4100
4100-4200
4200-4300
4300-4400
4400-4500
4500-4600
4600-4700
4700-4800
4800-4900
4900-5000
5000-5100
5100-5200
5200-5300
5300-5400
5400-5500
5500-5600
5600-5700
5700-5800
5800-5900
5900-6000
6000-6100
6100-6200
6200-6300
6300-6400
6400-6500
6500-6600
6600-6700
6700-6800
6800-6900
6900-7000
7000-7100
7100-7200
7200-7300
7300-7400
7400-7500
7500-7600
7600-7700
7700-7800
7800-7900
7900-8000


In [291]:
#print 
print(f"Total entries in starting dataframe: {len(set(shuffled.index.tolist()))}") 
print(f"Number of sampled dataframe: {len(sampled_dfs)}")
print(f"Length of each dataframe: {len(sampled_dfs[-1])}")

Total entries in starting dataframe: 8061
Number of sampled dataframe: 80
Length of each dataframe: 100


In [294]:
#check if ids overlap
total_ids = []
for d in sampled_dfs:
    for i in d.index.to_list():
        total_ids.append(i)
assert len(total_ids) == len(set(total_ids)), "Ids overlap!"
print(f"Sanity check for ids overalapping: OK")


Sanity check for ids overalapping: OK


In [295]:
with open("../manual_evaluation/all_rand_subsets.pkl", "wb") as outfile:
    pickle.dump(sampled_dfs, outfile)


In [296]:
for i in man_eval_inputs:
    print(i, "\n\n\n\n")

Art. 1 Capacità giuridica
La capacità giuridica si acquista dal momento della nascita.I diritti che la legge riconosce a favore del concepito sono subordinati all’evento della nascita.

Domanda:
Quando si acquisisce la capacità giuridica? 




Art. 1 Capacità giuridica
La capacità giuridica si acquista dal momento della nascita.I diritti che la legge riconosce a favore del concepito sono subordinati all’evento della nascita.

Domanda:
A quale condizione sono subordinati i diritti riconosciuti al concepito dalla legge? 




Art. 2 Maggiore età. Capacità di agire
La maggiore età è fissata al compimento del diciottesimo anno. Con la maggiore età si acquista la capacità di compiere tutti gli atti per i quali non sia stabilita una età diversa.Sono salve le leggi speciali che stabiliscono un’età inferiore in materia di capacità a prestare il proprio lavoro.In tal caso il minore è abilitato all’esercizio dei diritti e delle azioni che dipendono dal contratto di lavoro.

Domanda:
A quale età s

In [ ]:
#save 5 random subset dfs ready for evaluation

rand_ids = random.sample(range(80), 5)
for id in rand_ids:
    print(f"Saving random sampled dataframe {id}")
    sampled_dfs[id].to_csv(f"../manual_evaluation/man_eval_randss_{id}.tsv", sep = "\t")
    with open("../manual_evaluation/evaluated_dfs_log.txt", "a") as f:
        f.write(str(id) +",")


Saving random sampled dataframe 14
Saving random sampled dataframe 3
Saving random sampled dataframe 35
Saving random sampled dataframe 31
Saving random sampled dataframe 28


In [ ]:
# initial_questions = 
df = pd.read_csv("../manual_evaluation/form_prova.tsv", sep = "\t")
len([i[-1][0] for i in list(df.T.iterrows())[3:]])

100